# Transform delta tables and create gold tables for star schema

In [0]:
from pyspark.sql.functions import explode, sequence, to_date

beginDate = '2010-01-01'
endDate = '2023-12-31'


spark.sql(f"select explode(sequence(to_date('{beginDate}'), to_date('{endDate}'), interval 1 day)) as date").createOrReplaceTempView('dates_tmp')


In [0]:
%sql 

create or replace table gold_dates using delta location '/delta/dates' 
as select 
date, day(date) as day, date_format(date, 'EEEE') as day_name, weekday(date) + 1 as day_of_week, month(date) as month, year(date) as year 
from dates_tmp

num_affected_rows num_inserted_rows

In [0]:
riders_df = spark.table("silver_riders")
dim_riders_df = riders_df \
    .withColumnRenamed('account_start_date', "member_start_date_id") \
    .withColumnRenamed('account_end_date', "member_end_date_id") \
    .select("rider_id", "first_name", "last_name", "address", "birthday", "is_member", "member_start_date_id", "member_end_date_id")
dim_riders_df.dropDuplicates(["rider_id"]).write.format("delta").mode("overwrite").saveAsTable("gold_riders")

In [0]:
stations_df = spark.table("silver_stations")
dim_stations_df = stations_df.select("station_id","name","latitude", "longitude")
dim_stations_df.dropDuplicates(["station_id"]).write.format("delta").mode("overwrite").saveAsTable("gold_stations")


In [0]:
payments_df = spark.table("silver_payments")
fact_payments_df = payments_df \
    .withColumn("date_id", payments_df.date) \
    .select("payment_id","rider_id","date_id","amount")
fact_payments_df.dropDuplicates(["payment_id"]).write.format("delta").mode("overwrite").saveAsTable("gold_payments")


In [0]:
from pyspark.sql.functions import datediff,col, unix_timestamp, round
from pyspark.sql.types import IntegerType

trips_df = spark.table("silver_trips")
fact_trips_df = trips_df.join(riders_df, trips_df.rider_id == riders_df.rider_id, "left") \
    .withColumn("trip_duration_minutes",round((unix_timestamp("ended_at") - unix_timestamp('start_at'))/60)) \
    .withColumn('rider_age', round(datediff(col("account_start_date"),col("birthday"))/365.25).cast('int')) \
    .withColumnRenamed("start_at","start_date_id") \
    .withColumnRenamed("ended_at","end_date_id") \
    .select("trip_id", "trip_duration_minutes", "start_date_id", "end_date_id", trips_df.rider_id, col("rider_age"), "rideable_type", "start_station_id", "end_station_id")

display(fact_trips_df)

fact_trips_df.dropDuplicates(["trip_id"]).write.format("delta").mode("overwrite").saveAsTable("gold_trips")

trip_id trip_duration_minutes start_date_id end_date_id rider_id rider_age rideable_type start_station_id end_station_id 89E7AA6C29227EFF 7.0 2021-02-12T16:14:56.000+0000 2021-02-12T16:21:43.000+0000 71934 37 classic_bike 525 660 0FEFDE2603568365 20.0 2021-02-14T17:52:38.000+0000 2021-02-14T18:12:09.000+0000 47854 37 classic_bike 525 16806 E6159D746B2DBB91 9.0 2021-02-09T19:10:18.000+0000 2021-02-09T19:19:10.000+0000 70870 33 electric_bike KA1503000012 TA1305000029 B32D3199F1C2E75B 4.0 2021-02-02T17:49:41.000+0000 2021-02-02T17:54:06.000+0000 58974 19 classic_bike 637 TA1305000034 83E463F23575F4BF 15.0 2021-02-23T15:07:23.000+0000 2021-02-23T15:22:37.000+0000 39608 71 electric_bike 13216 TA1309000055 BDAA7E3494E8D545 6.0 2021-02-24T15:43:33.000+0000 2021-02-24T15:49:05.000+0000 36267 28 electric_bike 18003 KP1705001026 A772742351171257 1.0 2021-02-01T17:47:42.000+0000 2021-02-01T17:48:33.000+0000 50104 29 classic_bike KP1705001026 KP1705001026 295476889D9B79F8 1.0 2021-02-11T18:33:53.000+0000 2021-02-11T18:35:09.000+0000 19618 21 classic_bike 18003 18003 362087194BA4CC9A 23.0 2021-02-27T15:13:39.000+0000 2021-02-27T15:36:36.000+0000 16732 15 classic_bike KP1705001026 KP1705001026 21630F715038CCB0 17.0 2021-02-20T08:59:42.000+0000 2021-02-20T09:17:04.000+0000 57068 45 classic_bike KP1705001026 KP1705001026 A977EB7FE7F5CD3A 0.0 2021-02-20T08:58:16.000+0000 2021-02-20T08:58:41.000+0000 32712 16 classic_bike KP1705001026 KP1705001026 8B868B03D6753C2A 15.0 2021-02-20T16:45:11.000+0000 2021-02-20T16:59:47.000+0000 23227 25 classic_bike KP1705001026 KP1705001026 BD331D658B9D2C31 4.0 2021-02-18T13:21:03.000+0000 2021-02-18T13:25:20.000+0000 73221 16 classic_bike 525 520 8DFEA9BAFE6BAA62 3.0 2021-02-26T17:40:05.000+0000 2021-02-26T17:42:49.000+0000 22163 42 classic_bike 13253 TA1309000050 27BE9F6E67AFD86C 15.0 2021-02-06T14:40:25.000+0000 2021-02-06T14:55:50.000+0000 7566 22 classic_bike 525 15578 9B790D47A0A0F7F1 44.0 2021-02-19T23:25:40.000+0000 2021-02-20T00:10:00.000+0000 71588 18 classic_bike KA1503000044 KA1504000142 3C2DF72600B1DE6C 41.0 2021-02-18T23:20:10.000+0000 2021-02-19T00:01:39.000+0000 38661 33 classic_bike KA1503000044 KA1504000142 48A8D07ED9C7065C 42.0 2021-02-20T23:35:29.000+0000 2021-02-21T00:17:18.000+0000 64751 24 classic_bike KA1503000044 KA1504000142 BBFF2AAA0A3A1A26 15.0 2021-02-02T15:48:52.000+0000 2021-02-02T16:03:40.000+0000 10721 26 electric_bike KA1504000140 17660 030723CBA8CF05E7 5.0 2021-02-23T07:44:12.000+0000 2021-02-23T07:48:57.000+0000 13281 23 classic_bike TA1305000032 15542 7DF4C2D21E1DDD46 30.0 2021-02-09T14:00:06.000+0000 2021-02-09T14:30:29.000+0000 39717 25 classic_bike 525 605 2C4AF52044E874FC 12.0 2021-02-26T18:16:25.000+0000 2021-02-26T18:27:55.000+0000 39561 44 electric_bike TA1306000012 SL-007 6E944BAF2AB37023 29.0 2021-02-24T17:09:22.000+0000 2021-02-24T17:38:15.000+0000 22386 25 classic_bike 525 TA1307000144 3CDFBD181A0EDB00 4.0 2021-02-23T11:28:45.000+0000 2021-02-23T11:32:39.000+0000 9130 37 classic_bike KA1503000044 TA1307000151 96F92F578CD76F59 0.0 2021-02-27T13:32:44.000+0000 2021-02-27T13:32:58.000+0000 9578 31 classic_bike 637 637 42B25557198348CC 16.0 2021-02-23T16:05:02.000+0000 2021-02-23T16:20:35.000+0000 44811 25 classic_bike 13133 13133 AD6C500EEAD6B929 45.0 2021-02-27T16:14:45.000+0000 2021-02-27T16:59:59.000+0000 5515 35 classic_bike SL-005 SL-005 3158E663B4F160EB 0.0 2021-02-27T15:38:05.000+0000 2021-02-27T15:38:22.000+0000 2437 35 classic_bike 13235 13235 78849DFCC4D4B7A0 75.0 2021-02-28T13:31:50.000+0000 2021-02-28T14:47:14.000+0000 18861 19 classic_bike 13235 13235 1F3946A6B0E9AC91 0.0 2021-02-01T15:08:37.000+0000 2021-02-01T15:08:59.000+0000 42244 21 classic_bike TA1307000139 TA1307000139 F6ABBD3E1BDA78A6 0.0 2021-02-11T11:46:46.000+0000 2021-02-11T11:46:48.000+0000 53164 23 classic_bike TA1307000139 TA1307000139 D5171DFF5A12AD19 1.0 2021-02-02T17:27:52.000+0000 2021-02-02T17:28:28.000+0000 62292 35 classic_bike TA1307000139 TA1307000139 BFFC6C2C4695FF77 11.0 2021-02-